# Imports

In [6]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import urllib.parse

import datetime
import os
import cloudscraper
import xlsxwriter
import time

# HTTP Request

## Store website in variable / Get Request with Cloud Scraper

In [2]:
site = 'https://www.autoevolution.com/cars/'
response = cloudscraper.CloudScraper().get(site)  # CloudScraper inherits from requests.Session

In [3]:
# response = requests.get(site)
# response = scraper.get(site)
# scraper = cloudscraper.create_scraper()  # returns a CloudScraper instance
# Or: scraper = cloudscraper.CloudScraper()  # CloudScraper inherits from requests.Session

# Target necessary data

In [4]:
# Brand / BrandLogoUrl / BrandLink
# Model / CarType / ModelYear / ModelImgUrl / ModelLink
# VariantBrand / VariantModel / VariantYear / VariantImgUrl / VariantLink
# BigImageBrand / BigImageTitle / BigImageUrl / BigImageThumb

# Brand Soup & Results & Status Code

In [5]:
soup = BeautifulSoup(response.content, 'html.parser')
results = soup.find_all('div', {'itemtype':'https://schema.org/Brand'})
print(response.status_code, " - ", len(results))
# results

200  -  118


## Brand / Logo URL / Link

In [6]:
i = 0
rBrand = results[i].find('a').get('title').replace(" models and specs", "") # brand
rBrandLogoUrl = results[i].find('img').get('src') # logo url
rBrandLink = results[i].find('a').get('href') # link

print(rBrand, "\n", rBrandLogoUrl, "\n", rBrandLink)

AC  
 https://s1.cdn.autoevolution.com/images/producers/ac-sm.jpg 
 https://www.autoevolution.com/ac/


# Model Soup & Results

In [7]:
responseModel = cloudscraper.CloudScraper().get(rBrandLink)
soupModel = BeautifulSoup(responseModel.content, 'html.parser')
resultsModel = soupModel.find_all('div', {'class':'carmod'})
print(responseModel.status_code, " - ", len(resultsModel))
# soupModel

200  -  5


## Model / CarType / Year / Image URL / Link

In [13]:
i = 0
rModel = resultsModel[i].find('h4').get_text() # model
rCarType = resultsModel[i].find('p', {'class':'body'}).get_text() # car type
rmYear = resultsModel[i].find('div', {'class':'col3width fl'}).find('span').get_text() # year
rmImageUrl = resultsModel[i].find('img').get('src') # image url
rmLink = resultsModel[i].find('a').get('href') # link

print(rModel, "\n", rCarType, "\n", rmYear, "\n", rmImageUrl, "\n", rmLink)

AC  Ace 
 convertibles 
 1993 - 1996 
 https://s1.cdn.autoevolution.com/images/models/thumb/AC-_Ace-1993_main.jpg_tmb.jpg 
 https://www.autoevolution.com/ac/ace/


# Variant Soup & Results

In [16]:
responseVariant = cloudscraper.CloudScraper().get(rmLink)
soupVariant = BeautifulSoup(responseVariant.content, 'html.parser')
resultsVariant = soupVariant.find_all('div', {'class':'container carmodel clearfix'})
print(responseVariant.status_code, " - ", len(resultsVariant))
# resultsVariant

200  -  1


## Brand / Model / Year / Image URL / Link

In [17]:
i = 0
rvBrand = resultsVariant[i].find('b', {'itemprop':'brand'}).get_text() # brand
rvModel = resultsVariant[i].find('span', {'class':'col-red'}).get_text() # model
rvYear = resultsVariant[i].find('p', {'class':'years'}).find('a').get_text() # year
rvImageUrl = resultsVariant[i].find('img', {'itemprop':'image'}).get('src') # image url
bigImageLink = resultsVariant[i].find('a', {'itemprop':'url'}).get('href') # link

print(rvBrand, "\n", rvModel, "\n", rvYear, "\n", rvImageUrl, "\n", bigImageLink)

AC  
 Ace 
 1993 - 1996 
 https://s1.cdn.autoevolution.com/images/models/AC-_Ace-1993_main.jpg 
 https://www.autoevolution.com/cars/ac-ace-1993.html


# Big Image Soup & Results

In [19]:
responseBigImage = cloudscraper.CloudScraper().get(bigImageLink)
soupBigImage = BeautifulSoup(responseBigImage.content, 'html.parser')
resultsBigImage = soupBigImage.find('div', {'data-itemtype':'https://schema.org/Car'}).find_all('a', {'class':'s_gallery'})
print(responseBigImage.status_code, " - ", len(resultsBigImage))
resultsBigImage[0]

200  -  6


<a class="s_gallery" href="https://s1.cdn.autoevolution.com/images/gallery/ac-ace-1993-7215_1.jpg" id="aegal_0" rel="noopener" target="_blank" title="AC  Ace (1993 - 1996)"><img alt="AC  Ace (1993 - 1996)" data-description="Photo credits: AC " data-gidm="236475" data-gidx="0" data-title="AC  Ace (1993 - 1996)" decoding="async" loading="lazy" src="https://s1.cdn.autoevolution.com/images/cars-gallery-149x/ac-ace-1993-thumbnail-7215_1.jpg"/></a>

## Brand / Title / Image URL

In [20]:
for i in range(len(resultsBigImage)):
    print(resultsBigImage[i].find('img').get('data-description').replace("Photo credits: ", "")) # brand
    print(resultsBigImage[i].get('title')) # title
    print(resultsBigImage[i].get('href')) # big image
    print(resultsBigImage[i].find('img').get('src')) # big image thumbnail

AC 
AC  Ace (1993 - 1996)
https://s1.cdn.autoevolution.com/images/gallery/ac-ace-1993-7215_1.jpg
https://s1.cdn.autoevolution.com/images/cars-gallery-149x/ac-ace-1993-thumbnail-7215_1.jpg
AC 
AC  Ace (1993 - 1996)
https://s1.cdn.autoevolution.com/images/gallery/ac-ace-1993-7215_2.jpg
https://s1.cdn.autoevolution.com/images/cars-gallery-149x/ac-ace-1993-thumbnail-7215_2.jpg
AC 
AC  Ace (1993 - 1996)
https://s1.cdn.autoevolution.com/images/gallery/ac-ace-1993-7215_3.jpg
https://s1.cdn.autoevolution.com/images/cars-gallery-149x/ac-ace-1993-thumbnail-7215_3.jpg
AC 
AC  Ace (1993 - 1996)
https://s1.cdn.autoevolution.com/images/gallery/ac-ace-1993-7215_4.jpg
https://s1.cdn.autoevolution.com/images/cars-gallery-149x/ac-ace-1993-thumbnail-7215_4.jpg
AC 
AC  Ace (1993 - 1996)
https://s1.cdn.autoevolution.com/images/gallery/ac-ace-1993-7215_5.jpg
https://s1.cdn.autoevolution.com/images/cars-gallery-149x/ac-ace-1993-thumbnail-7215_5.jpg
AC 
AC  Ace (1993 - 1996)
https://s1.cdn.autoevolution.com/i

# Put everything together inside a For-Loop

## Brand Loop

In [21]:
# Brand / BrandLogoUrl / BrandLink
brandList = []
brandLogoUrlList = []
brandLinkList = []

brandList.clear()
brandLogoUrlList.clear()
brandLinkList.clear()

for i in range(len(results)):
    
    print(results[i].find('a').get('title').replace(" models and specs", "")) # brand
    try:
        brandList.append(results[i].find('a').get('title').replace(" models and specs", ""))
    except:
        brandList.append('n/a')

    print(results[i].find('img').get('src')) # brand logo url
    try:
        brandLogoUrlList.append(results[i].find('img').get('src'))
    except:
        brandLogoUrlList.append('n/a')

    print(results[i].find('a').get('href')) # brand link
    try:
        brandLinkList.append(results[i].find('a').get('href'))
    except:
        brandLinkList.append('n/a')


AC 
https://s1.cdn.autoevolution.com/images/producers/ac-sm.jpg
https://www.autoevolution.com/ac/
ACURA
https://s1.cdn.autoevolution.com/images/producers/acura-sm.jpg
https://www.autoevolution.com/acura/
ALFA ROMEO
https://s1.cdn.autoevolution.com/images/producers/alfa-romeo-sm.jpg
https://www.autoevolution.com/alfa-romeo/
ALPINE
https://s1.cdn.autoevolution.com/images/producers/alpine-sm.jpg
https://www.autoevolution.com/alpine/
ARIEL
https://s1.cdn.autoevolution.com/images/producers/ariel-sm.jpg
https://www.autoevolution.com/ariel/
ARO
https://s1.cdn.autoevolution.com/images/producers/aro-sm.jpg
https://www.autoevolution.com/aro/
ARTEGA
https://s1.cdn.autoevolution.com/images/producers/artega-sm.jpg
https://www.autoevolution.com/artega/
ASTON MARTIN
https://s1.cdn.autoevolution.com/images/producers/aston-martin-sm.jpg
https://www.autoevolution.com/aston-martin/
AUDI
https://s1.cdn.autoevolution.com/images/producers/audi-sm.jpg
https://www.autoevolution.com/audi/
AURUS
https://s1.cdn.

## Model Loop

In [22]:
# (Brand) / Model / CarType / ModelYear / ModelImgUrl / ModelLink
mBrandList = []
modelList = []
carTypeList = []
mYearList = []
mImgUrlList = []
mLinkList = []

mBrandList.clear()
modelList.clear()
carTypeList.clear()
mYearList.clear()
mImgUrlList.clear()
mLinkList.clear()

for i in range(len(results)):
    for x in range(9):
        print('x değeri: ', x)
    
        print("Brand: ", brandList[i])
        responseModel = cloudscraper.CloudScraper().get(brandLinkList[i])
        soupModel = BeautifulSoup(responseModel.content, 'html.parser')
        resultsModel = soupModel.find_all('div', {'class':'carmod'})
        
        if len(resultsModel) != 0:
            
            for j in range(len(resultsModel)):

                print(brandList[i]) # brand
                try:
                    mBrandList.append(brandList[i])
                except:
                    mBrandList.append('n/a')

                print(resultsModel[j].find('h4').get_text()) # model
                try:
                    modelList.append(resultsModel[j].find('h4').get_text())
                except:
                    modelList.append('n/a')

                print(resultsModel[j].find('p', {'class':'body'}).get_text()) # car type
                try:
                    carTypeList.append(resultsModel[j].find('p', {'class':'body'}).get_text())
                except:
                    carTypeList.append('n/a')

                print(resultsModel[j].find('div', {'class':'col3width fl'}).find('span').get_text()) # model year
                try:
                    mYearList.append(resultsModel[j].find('div', {'class':'col3width fl'}).find('span').get_text())
                except:
                    mYearList.append('n/a')

                print(resultsModel[j].find('img').get('src')) # model image url
                try:
                    mImgUrlList.append(resultsModel[j].find('img').get('src'))
                except:
                    mImgUrlList.append('n/a')

                print(resultsModel[j].find('a').get('href')) # model link
                try:
                    mLinkList.append(resultsModel[j].find('a').get('href'))
                except:
                    mLinkList.append('n/a')
                print('for döngüsü çalıştı')
            
            break
        
        elif len(resultsModel) == 0:
            print('continue, else if çalıştı')
            continue
        else:
            print('break, else bloğu çalıştı')
            break


x değeri:  0
Brand:  AC 
AC 
AC  Ace
convertibles
1993 - 1996
https://s1.cdn.autoevolution.com/images/models/thumb/AC-_Ace-1993_main.jpg_tmb.jpg
https://www.autoevolution.com/ac/ace/
for döngüsü çalıştı
AC 
AC  Aceca
coupes
1998 - 2000
https://s1.cdn.autoevolution.com/images/models/thumb/AC-_Aceca-1998_main.jpg_tmb.jpg
https://www.autoevolution.com/ac/aceca/
for döngüsü çalıştı
AC 
AC  Cobra
coupes
1965 - 1967
https://s1.cdn.autoevolution.com/images/models/thumb/AC-_Cobra-378-MkIV-2020_main.jpg_tmb.jpg
https://www.autoevolution.com/ac/cobra/
for döngüsü çalıştı
AC 
AC  Frua Convertible
convertibles
1966 - 1971
https://s1.cdn.autoevolution.com/images/models/thumb/AC-_428-Convertible-1966_main.jpg_tmb.jpg
https://www.autoevolution.com/ac/frua-convertible/
for döngüsü çalıştı
AC 
AC  Frua Coupe
coupes
1966 - 1973
https://s1.cdn.autoevolution.com/images/models/thumb/AC-_428-Coupe-1966_main.jpg_tmb.jpg
https://www.autoevolution.com/ac/frua-coupe/
for döngüsü çalıştı
x değeri:  0
Brand:  ACU

ALPINE
ALPINE A110S
coupes
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/ALPINE_A110S-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/alpine/a110s/
for döngüsü çalıştı
ALPINE
ALPINE A110
coupes
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/ALPINE_A110-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/alpine/a110/
for döngüsü çalıştı
ALPINE
ALPINE A106
coupes
1955 - 1964
https://s1.cdn.autoevolution.com/images/models/thumb/ALPINE_A106-1955_main.jpg_tmb.jpg
https://www.autoevolution.com/alpine/a106/
for döngüsü çalıştı
ALPINE
ALPINE A108
coupes
1958 - 1965
https://s1.cdn.autoevolution.com/images/models/thumb/ALPINE_A108-1958_main.jpg_tmb.jpg
https://www.autoevolution.com/alpine/a108/
for döngüsü çalıştı
x değeri:  0
Brand:  ARIEL
continue, else if çalıştı
x değeri:  1
Brand:  ARIEL
ARIEL
ARIEL Atom
convertibles
2011 - present
https://s1.cdn.autoevolution.com/images/models/thumb/ARIEL_Atom-500-V8-2011_main.png_tmb.png
https://www.autoevolu

AUDI
AUDI R8
coupes
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/AUDI_R8-V10-performance-RWD-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/audi/r8/
for döngüsü çalıştı
AUDI
AUDI S8
sedans
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/AUDI_S8-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/audi/s8/
for döngüsü çalıştı
AUDI
AUDI A3 Sedan
sedans
2020 - present
https://s1.cdn.autoevolution.com/images/models/thumb/AUDI_A3-Sedan-2020_main.jpg_tmb.jpg
https://www.autoevolution.com/audi/a3-sedan/
for döngüsü çalıştı
AUDI
AUDI A3 Sportback
hatchbacks
2020 - present
https://s1.cdn.autoevolution.com/images/models/thumb/AUDI_A3-Sportback-2020_main.jpg_tmb.jpg
https://www.autoevolution.com/audi/a3-sportback/
for döngüsü çalıştı
AUDI
AUDI RS 3 Sedan
sedans
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/AUDI_RS-3-Sedan-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/audi/rs3-sedan/
for döngüsü çalıştı
AUDI
AUDI S5 Sportba

AURUS
AURUS Senat
sedans
2018 - present
https://s1.cdn.autoevolution.com/images/models/thumb/AURUS_Senat-2018_main.jpg_tmb.jpg
https://www.autoevolution.com/aurus/senat/
for döngüsü çalıştı
x değeri:  0
Brand:  BENTLEY
BENTLEY
BENTLEY Bentayga
suvs
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/BENTLEY_Bentayga-S-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/bentley/bentayga/
for döngüsü çalıştı
BENTLEY
BENTLEY Bentayga Speed
suvs
2020 - present
https://s1.cdn.autoevolution.com/images/models/thumb/BENTLEY_Bentayga-Speed-2020_main.jpg_tmb.jpg
https://www.autoevolution.com/bentley/bentayga-speed/
for döngüsü çalıştı
BENTLEY
BENTLEY Flying Spur
sedans
2019 - present
https://s1.cdn.autoevolution.com/images/models/thumb/BENTLEY_Flying-Spur-2019_main.jpg_tmb.jpg
https://www.autoevolution.com/bentley/flying-spur-1/
for döngüsü çalıştı
BENTLEY
BENTLEY Continental GTC
convertibles
2018 - present
https://s1.cdn.autoevolution.com/images/models/thumb/BENTLEY_Continental-

continue, else if çalıştı
x değeri:  1
Brand:  BRISTOL
BRISTOL
BRISTOL Bullet
convertibles
2017 - present
https://s1.cdn.autoevolution.com/images/models/thumb/BRISTOL_Bullet-2017_main.jpg_tmb.jpg
https://www.autoevolution.com/bristol/bullet/
for döngüsü çalıştı
BRISTOL
BRISTOL 400
coupes
1946 - 1950
https://s1.cdn.autoevolution.com/images/models/thumb/BRISTOL_Type-400-1946_main.jpg_tmb.jpg
https://www.autoevolution.com/bristol/400/
for döngüsü çalıştı
BRISTOL
BRISTOL 402
convertibles
1949 - 1950
https://s1.cdn.autoevolution.com/images/models/thumb/BRISTOL_402-1949_main.jpg_tmb.jpg
https://www.autoevolution.com/bristol/402/
for döngüsü çalıştı
BRISTOL
BRISTOL 403
coupes
1953 - 1955
https://s1.cdn.autoevolution.com/images/models/thumb/BRISTOL_403-1953_main.jpg_tmb.jpg
https://www.autoevolution.com/bristol/403/
for döngüsü çalıştı
BRISTOL
BRISTOL 404
coupes
1953 - 1955
https://s1.cdn.autoevolution.com/images/models/thumb/BRISTOL_404-1953_main.jpg_tmb.jpg
https://www.autoevolution.com/bris

...

TESLA MOTORS
TESLA MOTORS Model S
sedans
2016 - present
https://s1.cdn.autoevolution.com/images/models/thumb/TESLA-MOTORS_Model-S-2016_main.jpg_tmb.jpg
https://www.autoevolution.com/tesla-motors/model-s/
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster
convertibles
2018 - present
https://s1.cdn.autoevolution.com/images/models/thumb/TESLA-MOTORS_Roadster-2018_main.jpg_tmb.jpg
https://www.autoevolution.com/tesla-motors/roadster-2/
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Model 3
sedans
2017 - present
https://s1.cdn.autoevolution.com/images/models/thumb/TESLA-MOTORS_Model-3-2017_main.jpg_tmb.jpg
https://www.autoevolution.com/tesla-motors/model-3/
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Cybertruck
trucks
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/TESLA-MOTORS_Cybertruck-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/tesla-motors/cybertruck/
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Model Y
suvs
2019 - present
https://s1.cdn.autoevolution.c

continue, else if çalıştı
x değeri:  1
Brand:  TVR
TVR
TVR Griffith
convertibles
2017 - present
https://s1.cdn.autoevolution.com/images/models/thumb/TVR_Griffith-2017_main.jpg_tmb.jpg
https://www.autoevolution.com/tvr/griffith/
for döngüsü çalıştı
TVR
TVR "Wedge Series"
convertibles
1983 - 1987
https://s1.cdn.autoevolution.com/images/models/thumb/TVR_280i--350i-Convertible-1983_main.jpg_tmb.jpg
https://www.autoevolution.com/tvr/wedge-series/
for döngüsü çalıştı
TVR
TVR Cerbera
coupes
2000 - 2004
https://s1.cdn.autoevolution.com/images/models/thumb/TVR_Cerbera-2000_main.jpg_tmb.jpg
https://www.autoevolution.com/tvr/cerbera/
for döngüsü çalıştı
TVR
TVR Chimaera
convertibles
1992 - 2001
https://s1.cdn.autoevolution.com/images/models/thumb/TVR_Chimaera-1992_main.jpg_tmb.jpg
https://www.autoevolution.com/tvr/chimaera/
for döngüsü çalıştı
TVR
TVR Sagaris
coupes
2004 - 2006
https://s1.cdn.autoevolution.com/images/models/thumb/TVR_Sagaris-2004_main.jpg_tmb.jpg
https://www.autoevolution.com/tvr

continue, else if çalıştı
x değeri:  1
Brand:  VOLKSWAGEN
VOLKSWAGEN
VOLKSWAGEN T-Roc
suvs
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLKSWAGEN_T-Roc-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/volkswagen/t-roc/
for döngüsü çalıştı
VOLKSWAGEN
VOLKSWAGEN Golf R Variant
wagons
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLKSWAGEN_Golf-R-Variant-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/volkswagen/golf-r-variant/
for döngüsü çalıştı
VOLKSWAGEN
VOLKSWAGEN Jetta / Vento / Bora
sedans
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLKSWAGEN_Jetta-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/volkswagen/jetta-vento-bora/
for döngüsü çalıştı
VOLKSWAGEN
VOLKSWAGEN T-Roc R
suvs
2021 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLKSWAGEN_T-Roc-R-2021_main.jpg_tmb.jpg
https://www.autoevolution.com/volkswagen/t-roc-r/
for döngüsü çalıştı
VOLKSWAGEN
VOLKSWAGEN Polo 5 Doors
hatchbacks
2

VOLVO
VOLVO XC40
suvs
2022 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLVO_XC40-Recharge-2022_main.jpg_tmb.jpg
https://www.autoevolution.com/volvo/xc40/
for döngüsü çalıştı
VOLVO
VOLVO XC60 Polestar
suvs
2017 - 2021
https://s1.cdn.autoevolution.com/images/models/thumb/VOLVO_XC60-Polestar-2017_main.jpg_tmb.jpg
https://www.autoevolution.com/volvo/xc60-polestar/
for döngüsü çalıştı
VOLVO
VOLVO V90 Cross Country
wagons
2019 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLVO_V90-Cross-Country-2019_main.jpg_tmb.jpg
https://www.autoevolution.com/volvo/v90-cross-country/
for döngüsü çalıştı
VOLVO
VOLVO S90
sedans
2019 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLVO_S90-2019_main.jpg_tmb.jpg
https://www.autoevolution.com/volvo/s90/
for döngüsü çalıştı
VOLVO
VOLVO XC90
suvs
2019 - present
https://s1.cdn.autoevolution.com/images/models/thumb/VOLVO_XC90-2019_main.jpg_tmb.jpg
https://www.autoevolution.com/volvo/xc90/
for döngüsü çalıştı
VO

continue, else if çalıştı
x değeri:  1
Brand:  WIESMANN
continue, else if çalıştı
x değeri:  2
Brand:  WIESMANN
WIESMANN
WIESMANN GT MF5
coupes
2011 - present
https://s1.cdn.autoevolution.com/images/models/thumb/WIESMANN_GT-MF5-2011_main.jpg_tmb.jpg
https://www.autoevolution.com/wiesmann/gt-mf5/
for döngüsü çalıştı
WIESMANN
WIESMANN GT MF4
coupes
2010 - present
https://s1.cdn.autoevolution.com/images/models/thumb/WIESMANN_MF4-2010_main.jpg_tmb.jpg
https://www.autoevolution.com/wiesmann/gt-mf4/
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster
convertibles
2010 - present
https://s1.cdn.autoevolution.com/images/models/thumb/WIESMANN_MF4-Roadster-2011_main.jpg_tmb.jpg
https://www.autoevolution.com/wiesmann/mf4-roadster/
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster
convertibles
2012 - present
https://s1.cdn.autoevolution.com/images/models/thumb/WIESMANN_MF5-Roadster-2012_main.jpg_tmb.jpg
https://www.autoevolution.com/wiesmann/mf5-roadster/
for döngüsü çalıştı
WIESMANN
WIESMANN GT MF

## Variant Loop

In [16]:
# (Brand) / (Model) / (CarType) / (Year) / VariantImgUrl / VariantLink
vBrandList = []
vModelList = []
vCarTypeList = []
vYearList = []
vImgUrlList = []
vLinkList = []

vBrandList.clear()
vModelList.clear()
vCarTypeList.clear()
vYearList.clear()
vImgUrlList.clear()
vLinkList.clear()

for i in range(len(mLinkList)):
    for x in range(9):
        print('x değeri: ', x)
    
        print("Model: ", modelList[i])
        responseVariant = cloudscraper.CloudScraper().get(mLinkList[i])
        soupVariant = BeautifulSoup(responseVariant.content, 'html.parser')
        resultsVariant = soupVariant.find_all('div', {'class':'container carmodel clearfix'})
        
        if len(resultsVariant) != 0:
            
            for j in range(len(resultsVariant)):

                print(resultsVariant[j].find('b', {'itemprop':'brand'}).get_text()) # brand
                try:
                    vBrandList.append(resultsVariant[j].find('b', {'itemprop':'brand'}).get_text())
                except:
                    vBrandList.append('n/a')

                print(resultsVariant[j].find('span', {'class':'col-red'}).get_text()) # model
                try:
                    vModelList.append(resultsVariant[j].find('span', {'class':'col-red'}).get_text())
                except:
                    vModelList.append('n/a')

                print(carTypeList[i]) # car type
                try:
                    vCarTypeList.append(carTypeList[i])
                except:
                    vCarTypeList.append('n/a')

                print(resultsVariant[j].find('p', {'class':'years'}).find('a').get_text()) # year
                try:
                    vYearList.append(resultsVariant[j].find('p', {'class':'years'}).find('a').get_text())
                except:
                    vYearList.append('n/a')

                print(resultsVariant[j].find('img', {'itemprop':'image'}).get('src')) # image url
                try:
                    vImgUrlList.append(resultsVariant[j].find('img', {'itemprop':'image'}).get('src'))
                except:
                    vImgUrlList.append('n/a')

                print(resultsVariant[j].find('a', {'itemprop':'url'}).get('href')) # link
                try:
                    vLinkList.append(resultsVariant[j].find('a', {'itemprop':'url'}).get('href'))
                except:
                    vLinkList.append('n/a')
                print('for döngüsü çalıştı')
            
            break
        
        elif len(resultsVariant) == 0:
            print('continue, else if çalıştı')
            continue
        else:
            print('break, else bloğu çalıştı')
            break


Model:  LANCIA 2000 Coupe
LANCIA
2000 Coupe
coupes
1971 - 1974
https://s1.cdn.autoevolution.com/images/models/LANCIA_2000-Coupe-1971_main.jpg
https://www.autoevolution.com/cars/lancia-2000-coupe-1971.html
Model:  LANCIA A112
LANCIA
A112
hatchbacks
1982 - 1986
https://s1.cdn.autoevolution.com/images/models/LANCIA_A112-1982_main.jpg
https://www.autoevolution.com/cars/lancia-a112-1982.html
Model:  LANCIA A112 Abarth
LANCIA
A112 Abarth
hatchbacks
1984 - 1986
https://s1.cdn.autoevolution.com/images/models/LANCIA_A112-Abarth-1984_main.jpg
https://www.autoevolution.com/cars/lancia-a112-abarth-1984.html
Model:  LANCIA Alpha
LANCIA
Alpha
sedans
1907 - 1909
https://s1.cdn.autoevolution.com/images/models/LANCIA_Alpha-1907_main.jpg
https://www.autoevolution.com/cars/lancia-alpha-1907.html
Model:  LANCIA Aprilia
LANCIA
Aprilia
sedans
1937 - 1939
https://s1.cdn.autoevolution.com/images/models/LANCIA_Aprilia-1936_main.jpg
https://www.autoevolution.com/cars/lancia-aprilia-1936.html
Model:  LANCIA Arde

LANCIA
Musa
vans
2003 - 2012
https://s1.cdn.autoevolution.com/images/models/LANCIA_Musa-2003_main.jpg
https://www.autoevolution.com/cars/lancia-musa-2003.html
Model:  LANCIA Phedra
LANCIA
Phedra
vans
2002 - 2010
https://s1.cdn.autoevolution.com/images/models/LANCIA_Phedra-2002_main.jpg
https://www.autoevolution.com/cars/lancia-phedra-2002.html
Model:  LANCIA Prisma
LANCIA
Prisma
sedans
1983 - 1990
https://s1.cdn.autoevolution.com/images/models/LANCIA_Prisma-1983_main.jpg
https://www.autoevolution.com/cars/lancia-prisma-1983.html
Model:  LANCIA Stratos
LANCIA
Stratos
coupes
1973 - 1975
https://s1.cdn.autoevolution.com/images/models/LANCIA_Stratos-1973_main.jpg
https://www.autoevolution.com/cars/lancia-stratos-1973.html
Model:  LANCIA Thema
LANCIA
Thema
sedans
2011 - 2014
https://s1.cdn.autoevolution.com/images/models/LANCIA_Thema-2011_main.jpg
https://www.autoevolution.com/cars/lancia-thema-2011.html
LANCIA
Thema
sedans
1992 - 1995
https://s1.cdn.autoevolution.com/images/models/LANCIA_T

LAND ROVER
Range Rover PHEV
suvs
2017 - Present
https://s1.cdn.autoevolution.com/images/models/LAND-ROVER_Range-Rover-PHEV-2017_main.jpg
https://www.autoevolution.com/cars/land-rover-range-rover-phev-2017.html
LAND ROVER
Range Rover Hybrid
suvs
2013 - 2017
https://s1.cdn.autoevolution.com/images/models/LAND-ROVER_Range-Rover-PHEV-2014_main.jpg
https://www.autoevolution.com/cars/land-rover-range-rover-phev-2014.html
Model:  LAND ROVER Range Rover Sport
LAND ROVER
Range Rover Sport HST
suvs
2019 - Present
https://s1.cdn.autoevolution.com/images/models/LAND-ROVER_Range-Rover-Sport-HST-2019_main.jpg
https://www.autoevolution.com/cars/land-rover-range-rover-sport-hst-2019.html
LAND ROVER
Range Rover Sport
suvs
2017 - Present
https://s1.cdn.autoevolution.com/images/models/LAND-ROVER_Range-Rover-Sport-2017_main.jpg
https://www.autoevolution.com/cars/land-rover-range-rover-sport-2017.html
LAND ROVER
Range Rover Sport
suvs
2013 - 2017
https://s1.cdn.autoevolution.com/images/models/LAND-ROVER_Ra

LEXUS
LX
suvs
2021 - Present
https://s1.cdn.autoevolution.com/images/models/LEXUS_LX-2021_main.jpg
https://www.autoevolution.com/cars/lexus-lx-2021.html
LEXUS
LX
suvs
2015 - 2021
https://s1.cdn.autoevolution.com/images/models/LEXUS_LX-2015_main.jpg
https://www.autoevolution.com/cars/lexus-lx-2015.html
LEXUS
LX
suvs
2012 - 2015
https://s1.cdn.autoevolution.com/images/models/LEXUS_LX-2012_main.jpg
https://www.autoevolution.com/cars/lexus-lx-2012.html
LEXUS
LX
suvs
2008 - 2012
https://s1.cdn.autoevolution.com/images/models/LEXUS_Lexus-LX-2008_main.jpg
https://www.autoevolution.com/cars/lexus-lx-2008.html
LEXUS
LX
suvs
1997 - 2007
https://s1.cdn.autoevolution.com/images/models/LEXUS_LX-1997_main.jpg
https://www.autoevolution.com/cars/lexus-lx-1997.html
LEXUS
LX
suvs
1996 - 1997
https://s1.cdn.autoevolution.com/images/models/LEXUS_LX-1996_main.jpg
https://www.autoevolution.com/cars/lexus-lx-1996.html
Model:  LEXUS IS
LEXUS
IS
sedans
2020 - Present
https://s1.cdn.autoevolution.com/images/mod

LEXUS
HS 250h
sedans
2009 - 2013
https://s1.cdn.autoevolution.com/images/models/LEXUS_HS-250h-2009_main.jpg
https://www.autoevolution.com/cars/lexus-hs-250h-2009.html
Model:  LEXUS LFA
LEXUS
LFA
coupes
2010 - 2013
https://s1.cdn.autoevolution.com/images/models/LEXUS_LFA-2010_main.jpg
https://www.autoevolution.com/cars/lexus-lfa-2010.html
Model:  LEXUS SC
LEXUS
SC
coupes
2005 - 2010
https://s1.cdn.autoevolution.com/images/models/LEXUS_SC-2005_main.jpg
https://www.autoevolution.com/cars/lexus-sc-2005.html
LEXUS
SC
coupes
2001 - 2005
https://s1.cdn.autoevolution.com/images/models/LEXUS_SC-2001_main.jpg
https://www.autoevolution.com/cars/lexus-sc-2001.html
LEXUS
SC
coupes
1991 - 2000
https://s1.cdn.autoevolution.com/images/models/LEXUS_SC-1991_main.jpg
https://www.autoevolution.com/cars/lexus-sc-1991.html
Model:  LINCOLN Nautilus
LINCOLN
Nautilus
suvs
2020 - Present
https://s1.cdn.autoevolution.com/images/models/LINCOLN_Nautilius-2020_main.jpg
https://www.autoevolution.com/cars/lincoln-nau

...

VOLKSWAGEN
Touareg R
suvs
2020 - Present
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Touareg-R-2020_main.jpg
https://www.autoevolution.com/cars/volkswagen-touareg-r-2020.html
Model:  VOLKSWAGEN T-Cross
VOLKSWAGEN
T-Cross
suvs
2018 - Present
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_T-Cross-2018_main.jpg
https://www.autoevolution.com/cars/volkswagen-t-cross-2018.html
Model:  VOLKSWAGEN Arteon Shooting Brake
VOLKSWAGEN
Arteon Shooting Brake
wagons
2020 - Present
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Arteon-Shooting-Brake-2020_main.jpg
https://www.autoevolution.com/cars/volkswagen-arteon-shooting-brake-2020.html
VOLKSWAGEN
Arteon Shooting Brake R
wagons
2020 - Present
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Arteon-Shooting-Brake-R-2020_main.jpg
https://www.autoevolution.com/cars/volkswagen-arteon-shooting-brake-r-2020.html
Model:  VOLKSWAGEN Jetta GLI
VOLKSWAGEN
Jetta GLI
sedans
2021 - Present
https://s1.cdn.autoevolution

VOLKSWAGEN
Golf Plus
hatchbacks
2008 - 2013
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Golf-Plus-2008_main.jpg
https://www.autoevolution.com/cars/volkswagen-golf-plus-2008.html
VOLKSWAGEN
Golf Plus
hatchbacks
2005 - 2008
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Golf-Plus-2005_main.jpg
https://www.autoevolution.com/cars/volkswagen-golf-plus-2005.html
Model:  VOLKSWAGEN Golf R Cabrio
VOLKSWAGEN
Golf VI R Cabrio
convertibles
2013 - 2017
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Golf-R-Cabrio-2013_main.jpg
https://www.autoevolution.com/cars/volkswagen-golf-r-cabrio-2013.html
Model:  VOLKSWAGEN Lavida (China)
VOLKSWAGEN
Lavida
sedans
2008 - 2012
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Lavida-2008_main.jpg
https://www.autoevolution.com/cars/volkswagen-lavida-2008.html
Model:  VOLKSWAGEN Lupo
VOLKSWAGEN
Lupo GTI
hatchbacks
2002 - 2005
https://s1.cdn.autoevolution.com/images/models/VOLKSWAGEN_Lupo-GTI-2002_main.jpg
https://www.a

VOLVO
V90
wagons
2019 - Present
https://s1.cdn.autoevolution.com/images/models/VOLVO_V90-2019_main.jpg
https://www.autoevolution.com/cars/volvo-v90-2019.html
VOLVO
V90
wagons
2016 - 2019
https://s1.cdn.autoevolution.com/images/models/VOLVO_V90-2016_main.jpg
https://www.autoevolution.com/cars/volvo-v90-2016.html
VOLVO
V90
wagons
1997 - 1998
https://s1.cdn.autoevolution.com/images/models/VOLVO_V90-1997_main.jpg
https://www.autoevolution.com/cars/volvo-v90-1997.html
Model:  VOLVO V60
VOLVO
V60
wagons
2018 - Present
https://s1.cdn.autoevolution.com/images/models/VOLVO_V60-2018_main.jpg
https://www.autoevolution.com/cars/volvo-v60-2018.html
VOLVO
V60
wagons
2014 - 2018
https://s1.cdn.autoevolution.com/images/models/VOLVO_V60-2014_main.jpg
https://www.autoevolution.com/cars/volvo-v60-2014.html
VOLVO
V60
wagons
2010 - 2013
https://s1.cdn.autoevolution.com/images/models/VOLVO_V60-2010_main.jpg
https://www.autoevolution.com/cars/volvo-v60-2010.html
Model:  VOLVO S60
VOLVO
S60
sedans
2018 - Pres

VOLVO
940
sedans
1990 - 1997
https://s1.cdn.autoevolution.com/images/models/VOLVO_940-1990_main.jpg
https://www.autoevolution.com/cars/volvo-940-1990.html
Model:  VOLVO 940 Estate
VOLVO
940 Estate
wagons
1990 - 1998
https://s1.cdn.autoevolution.com/images/models/VOLVO_940-Estate-1990_main.jpg
https://www.autoevolution.com/cars/volvo-940-estate-1990.html
Model:  VOLVO 960
VOLVO
960
sedans
1994 - 1997
https://s1.cdn.autoevolution.com/images/models/VOLVO_960-1994_main.jpg
https://www.autoevolution.com/cars/volvo-960-1994.html
VOLVO
960
sedans
1990 - 1994
https://s1.cdn.autoevolution.com/images/models/VOLVO_960-1990_main.jpg
https://www.autoevolution.com/cars/volvo-960-1990.html
Model:  VOLVO 960 Estate
VOLVO
960 Estate
wagons
1994 - 1997
https://s1.cdn.autoevolution.com/images/models/VOLVO_960-Estate-1994_main.jpg
https://www.autoevolution.com/cars/volvo-960-estate-1994.html
Model:  VOLVO C30
VOLVO
C30
hatchbacks
2009 - 2013
https://s1.cdn.autoevolution.com/images/models/VOLVO_C30-2009_ma

WIESMANN
GT MF4-CS
coupes
2013 - Present
https://s1.cdn.autoevolution.com/images/models/WIESMANN_GT-MF4-CS-2013_main.jpg
https://www.autoevolution.com/cars/wiesmann-gt-mf4-cs-2013.html
Model:  WIESMANN MF4-S Roadster
WIESMANN
MF4-S Roadster
convertibles
2010 - Present
https://s1.cdn.autoevolution.com/images/models/WIESMANN_MF4-S-Roadster-2010_main.jpg
https://www.autoevolution.com/cars/wiesmann-mf4-s-roadster-2010.html
Model:  WIESMANN GT MF4-S
WIESMANN
MF4-S
coupes
2010 - Present
https://s1.cdn.autoevolution.com/images/models/WIESMANN_MF4-S-2010_main.jpg
https://www.autoevolution.com/cars/wiesmann-mf4-s-2010.html
Model:  ZENDER Escape 6
ZENDER
Escape 6

2000
https://s1.cdn.autoevolution.com/images/models/Zender_Escape-6-2000_main.jpg
https://www.autoevolution.com/cars/zender-escape-6-2000.html
Model:  ZENDER Fact 4 BiTurbo
ZENDER
Fact 4 BiTurbo

1989
https://s1.cdn.autoevolution.com/images/models/Zender_Fact-4-BiTurbo-1989_main.jpg
https://www.autoevolution.com/cars/zender-fact-4-bitu

# Import variant links from excel file

In [23]:
fileData = pd.read_excel (r'variantLink.xlsx', sheet_name='variant')
variantLinks = fileData['Variant Link'].values.tolist()

print (fileData)
# print (variantLinks)

print(len(variantLinks))

                                          Variant Link
0    https://www.autoevolution.com/cars/tesla-motor...
1    https://www.autoevolution.com/cars/tesla-motor...
2    https://www.autoevolution.com/cars/tesla-motor...
3    https://www.autoevolution.com/cars/tesla-motor...
4    https://www.autoevolution.com/cars/tesla-motor...
..                                                 ...
699  https://www.autoevolution.com/cars/zender-stra...
700  https://www.autoevolution.com/cars/zender-thir...
701  https://www.autoevolution.com/cars/zenvo-ts1-2...
702  https://www.autoevolution.com/cars/zenvo-tsr-s...
703  https://www.autoevolution.com/cars/zenvo-st1-2...

[704 rows x 1 columns]
704


## Big Images Loop

In [3]:
# BigImageBrand / BigImageTitle / BigImageUrl / BigImageThumb
bigImageBrand = []
bigImageTitle = []
bigImageUrl = []
# bigImageThumb = []

bigImageBrand.clear()
bigImageTitle.clear()
bigImageUrl.clear()
# bigImageThumb.clear()

for i in range(len(variantLinks)):
    
    for x in range(9):
        print('x değeri: ', x)
    
        print("Variant Link: ", variantLinks[i])
        responseBigImage = cloudscraper.CloudScraper().get(variantLinks[i])
        soupBigImage = BeautifulSoup(responseBigImage.content, 'html.parser')
        resultsBigImage = soupBigImage.find('div', {'data-itemtype':'https://schema.org/Car'}).find_all('a', {'class':'s_gallery'})
        print(responseBigImage.status_code, " - ", len(resultsBigImage))
        
        if len(resultsBigImage) != 0:
            for j in range(len(resultsBigImage)):
                
                print(resultsBigImage[j].find('img').get('data-description').replace("Photo credits: ", "")) # brand
                try:
                    bigImageBrand.append(resultsBigImage[j].find('img').get('data-description').replace("Photo credits: ", ""))
                except:
                    bigImageBrand.append('n/a')

                print(resultsBigImage[j].get('title')) # title
                try:
                    bigImageTitle.append(resultsBigImage[j].get('title'))
                except:
                    bigImageTitle.append('n/a')

                print(resultsBigImage[j].get('href')) # image url
                try:
                    bigImageUrl.append(resultsBigImage[j].get('href'))
                except:
                    bigImageUrl.append('n/a')

                # print(resultsBigImage[j].find('img').get('src')) # image thumbnail
                # try:
                #     bigImageThumb.append(resultsBigImage[j].find('img').get('src'))
                # except:
                #     bigImageThumb.append('n/a')
                print('for döngüsü çalıştı')
            
            break
        
        elif len(resultsBigImage) == 0:
            print('continue, else if çalıştı')
            continue
        else:
            print('break, else bloğu çalıştı')
            break


x değeri:  0
Variant Link:  https://www.autoevolution.com/cars/tesla-motors-roadster-2018.html
200  -  11
TESLA MOTORS
TESLA MOTORS Roadster (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TESLA-MOTORS-Roadster-6176_3.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TESLA-MOTORS-Roadster-6176_4.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TESLA-MOTORS-Roadster-6176_5.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TESLA-MOTORS-Roadster-6176_6.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TESLA-MOTORS-Roadster-6176_7.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TESLA-MOTORS-Roadster-6176_8.

200  -  16
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESLAMOTORSRoadster-3749_3.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESLAMOTORSRoadster-3749_4.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESLAMOTORSRoadster-3749_5.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESLAMOTORSRoadster-3749_6.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESLAMOTORSRoadster-3749_7.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESLAMOTORSRoadster-3749_8.jpg
for döngüsü çalıştı
TESLA MOTORS
TESLA MOTORS Roadster (2008 - 2012)
https://s1.cdn.autoevolution.com/images/gallery/TESL

200  -  57
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_28.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_29.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_30.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_31.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_32.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_33.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2022 - Present)
https://s1.cdn.autoevolution.com/images/gallery/toyota-sequoia-2022-7226_34.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Se

200  -  0
continue, else if çalıştı
x değeri:  3
Variant Link:  https://www.autoevolution.com/cars/toyota-trd-pro-2019.html
200  -  0
continue, else if çalıştı
x değeri:  4
Variant Link:  https://www.autoevolution.com/cars/toyota-trd-pro-2019.html
200  -  0
continue, else if çalıştı
x değeri:  5
Variant Link:  https://www.autoevolution.com/cars/toyota-trd-pro-2019.html
200  -  40
TOYOTA
TOYOTA TRD Pro (2019 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTA-TRD-Pro-6799_16.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA TRD Pro (2019 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTA-TRD-Pro-6799_17.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA TRD Pro (2019 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTA-TRD-Pro-6799_18.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA TRD Pro (2019 - Present)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTA-TRD-Pro-6799_19.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA TRD Pro (2019 - Present)
https://s1.cdn.autoevolution.com/images/ga

200  -  15
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_3.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_4.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_5.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_6.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_7.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_8.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TOYOTASequoia-3643_9.jpg
for döngüsü çalıştı
TOYOTA
TOYOTA Sequoia (2007 - 2017)
https://s1.cdn.autoevolution.com/images/gallery/TO

...

200  -  0
continue, else if çalıştı
x değeri:  1
Variant Link:  https://www.autoevolution.com/cars/wiesmann-gt-mf5-2008.html
200  -  0
continue, else if çalıştı
x değeri:  2
Variant Link:  https://www.autoevolution.com/cars/wiesmann-gt-mf5-2008.html
200  -  0
continue, else if çalıştı
x değeri:  3
Variant Link:  https://www.autoevolution.com/cars/wiesmann-gt-mf5-2008.html
200  -  13
WIESMANN
WIESMANN GT MF5 (2008 - 2011)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNGTMF5-4139_1.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN GT MF5 (2008 - 2011)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNGTMF5-4139_2.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN GT MF5 (2008 - 2011)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNGTMF5-4139_3.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN GT MF5 (2008 - 2011)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNGTMF5-4139_4.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN GT MF5 (2008 - 2011)
https://s1.cdn.autoevolution.com/images/gallery

200  -  22
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANN-MF4-Roadster-4968_1.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANN-MF4-Roadster-4968_2.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANN-MF4-Roadster-4968_3.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANN-MF4-Roadster-4968_4.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANN-MF4-Roadster-4968_5.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANN-MF4-Roadster-4968_6.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4 Roadster (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery

200  -  15
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_1.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_2.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_3.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_4.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_5.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_6.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF5 Roadster (2009 - 2010)
https://s1.cdn.autoevolution.com/images/gallery/WIESMANNMF5Roadster-4089_7.jpg
f

200  -  22
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_1.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_2.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_3.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_4.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_5.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_6.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.autoevolution.com/images/gallery/wiesmann-mf4-4966_7.jpg
for döngüsü çalıştı
WIESMANN
WIESMANN MF4-S (2010 - Present)
https://s1.cdn.au

200  -  46
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_1.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_2.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_3.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_4.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_5.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_6.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_7.jpg
for döngüsü çalıştı
Zenvo
Zenvo TSR-S (2018 - Present)
https://s1.cdn.autoevolution.com/images/gallery/Zenvo-TSR-S-6330_8.jpg
f

In [24]:
# Length brand arrays
print(len(brandList), len(brandLogoUrlList), len(brandLinkList))

118 118 118


# Create Pandas Brand Dataframe

In [25]:
# Create brand Pandas dataframes from brands.
brand_overview = pd.DataFrame({'Brand': brandList,
                               'Brand Logo URL': brandLogoUrlList,
                               'Brand Link': brandLinkList})
brand_overview

Brand                                     Brand Logo URL  \
0           AC   https://s1.cdn.autoevolution.com/images/produc...   
1         ACURA  https://s1.cdn.autoevolution.com/images/produc...   
2    ALFA ROMEO  https://s1.cdn.autoevolution.com/images/produc...   
3        ALPINE  https://s1.cdn.autoevolution.com/images/produc...   
4         ARIEL  https://s1.cdn.autoevolution.com/images/produc...   
..          ...                                                ...   
113  VOLKSWAGEN  https://s1.cdn.autoevolution.com/images/produc...   
114       VOLVO  https://s1.cdn.autoevolution.com/images/produc...   
115    WIESMANN  https://s1.cdn.autoevolution.com/images/produc...   
116      ZENDER  https://s1.cdn.autoevolution.com/images/produc...   
117       Zenvo  https://s1.cdn.autoevolution.com/images/produc...   

                                    Brand Link  
0            https://www.autoevolution.com/ac/  
1         https://www.autoevolution.com/acura/  
2    https://www.autoevolution.com/alfa-romeo/  
3        https://www.autoevolution.com/alpine/  
4         https://www.autoevolution.com/ariel/  
..                                         ...  
113  https://www.autoevolution.com/volkswagen/  
114       https://www.autoevolution.com/volvo/  
115    https://www.autoevolution.com/wiesmann/  
116      https://www.autoevolution.com/zender/  
117       https://www.autoevolution.com/zenvo/  

[118 rows x 3 columns]

In [26]:
# Length model arrays
print(len(mBrandList), len(modelList), len(carTypeList), len(mYearList), len(mImgUrlList), len(mLinkList))

2734 2734 2734 2734 2734 2734


# Create Pandas Model Dataframe

In [27]:
# Create model Pandas dataframes from models.
model_overview = pd.DataFrame({'Brand': mBrandList,
                               'Model': modelList,
                               'Car Type': carTypeList,
                               'Model Year': mYearList,
                               'Model Image URL': mImgUrlList,
                               'Model Link': mLinkList})
model_overview

Brand                 Model      Car Type      Model Year  \
0        AC                AC  Ace  convertibles     1993 - 1996   
1        AC              AC  Aceca        coupes     1998 - 2000   
2        AC              AC  Cobra        coupes     1965 - 1967   
3        AC   AC  Frua Convertible  convertibles     1966 - 1971   
4        AC         AC  Frua Coupe        coupes     1966 - 1973   
...      ...                   ...           ...             ...   
2729  ZENDER     ZENDER Straight 8                      2001 - 0   
2730  ZENDER       ZENDER Thirty 7                      1999 - 0   
2731   Zenvo             Zenvo TS1        coupes  2017 - present   
2732   Zenvo           Zenvo TSR-S                2018 - present   
2733   Zenvo             Zenvo ST1        coupes     2009 - 2017   

                                        Model Image URL  \
0     https://s1.cdn.autoevolution.com/images/models...   
1     https://s1.cdn.autoevolution.com/images/models...   
2     https://s1.cdn.autoevolution.com/images/models...   
3     https://s1.cdn.autoevolution.com/images/models...   
4     https://s1.cdn.autoevolution.com/images/models...   
...                                                 ...   
2729  https://s1.cdn.autoevolution.com/images/models...   
2730  https://s1.cdn.autoevolution.com/images/models...   
2731  https://s1.cdn.autoevolution.com/images/models...   
2732  https://s1.cdn.autoevolution.com/images/models...   
2733  https://s1.cdn.autoevolution.com/images/models...   

                                             Model Link  
0                 https://www.autoevolution.com/ac/ace/  
1               https://www.autoevolution.com/ac/aceca/  
2               https://www.autoevolution.com/ac/cobra/  
3     https://www.autoevolution.com/ac/frua-converti...  
4          https://www.autoevolution.com/ac/frua-coupe/  
...                                                 ...  
2729   https://www.autoevolution.com/zender/straight-8/  
2730     https://www.autoevolution.com/zender/thirty-7/  
2731           https://www.autoevolution.com/zenvo/ts1/  
2732         https://www.autoevolution.com/zenvo/tsr-s/  
2733           https://www.autoevolution.com/zenvo/st1/  

[2734 rows x 6 columns]

In [ ]:
# Length variant arrays
print(len(vBrandList), len(vModelList), len(vCarTypeList), len(vYearList), len(vImgUrlList), len(vLinkList))

# Create Pandas Variant Dataframe

In [22]:
# Create variant Pandas dataframes from variants.
variant_overview = pd.DataFrame({'Variant Brand': vBrandList,
                               'Variant Model': vModelList,
                               'Car Type': vCarTypeList,
                               'Variant Year': vYearList,
                               'Variant Image URL': vImgUrlList,
                               'Variant Link': vLinkList})
variant_overview

Variant Brand Variant Model    Car Type    Variant Year  \
0           LANCIA    2000 Coupe      coupes     1971 - 1974   
1           LANCIA          A112  hatchbacks     1982 - 1986   
2           LANCIA   A112 Abarth  hatchbacks     1984 - 1986   
3           LANCIA         Alpha      sedans     1907 - 1909   
4           LANCIA       Aprilia      sedans     1937 - 1939   
...            ...           ...         ...             ...   
3504        ZENDER    Straight 8                        2001   
3505        ZENDER      Thirty 7                        1999   
3506         Zenvo           TS1      coupes  2017 - Present   
3507         Zenvo         TSR-S              2018 - Present   
3508         Zenvo           ST1      coupes     2009 - 2017   

                                      Variant Image URL  \
0     https://s1.cdn.autoevolution.com/images/models...   
1     https://s1.cdn.autoevolution.com/images/models...   
2     https://s1.cdn.autoevolution.com/images/models...   
3     https://s1.cdn.autoevolution.com/images/models...   
4     https://s1.cdn.autoevolution.com/images/models...   
...                                                 ...   
3504  https://s1.cdn.autoevolution.com/images/models...   
3505  https://s1.cdn.autoevolution.com/images/models...   
3506  https://s1.cdn.autoevolution.com/images/models...   
3507  https://s1.cdn.autoevolution.com/images/models...   
3508  https://s1.cdn.autoevolution.com/images/models...   

                                           Variant Link  
0     https://www.autoevolution.com/cars/lancia-2000...  
1     https://www.autoevolution.com/cars/lancia-a112...  
2     https://www.autoevolution.com/cars/lancia-a112...  
3     https://www.autoevolution.com/cars/lancia-alph...  
4     https://www.autoevolution.com/cars/lancia-apri...  
...                                                 ...  
3504  https://www.autoevolution.com/cars/zender-stra...  
3505  https://www.autoevolution.com/cars/zender-thir...  
3506  https://www.autoevolution.com/cars/zenvo-ts1-2...  
3507  https://www.autoevolution.com/cars/zenvo-tsr-s...  
3508  https://www.autoevolution.com/cars/zenvo-st1-2...  

[3509 rows x 6 columns]

# Create Pandas Big Image Dataframe

In [29]:
# del bigImageBrand[:28840]
# del bigImageTitle[:28840]
# del bigImageUrl[:28840]
# del bigImageThumb[:28840]

In [6]:
# Create big image Pandas dataframes from big images.
bigImage_overview = pd.DataFrame({'Brand': bigImageBrand,
                               'Title': bigImageTitle,
                               'Image URL': bigImageUrl})
bigImage_overview

Brand                                   Title  \
0      TESLA MOTORS  TESLA MOTORS Roadster (2018 - Present)   
1      TESLA MOTORS  TESLA MOTORS Roadster (2018 - Present)   
2      TESLA MOTORS  TESLA MOTORS Roadster (2018 - Present)   
3      TESLA MOTORS  TESLA MOTORS Roadster (2018 - Present)   
4      TESLA MOTORS  TESLA MOTORS Roadster (2018 - Present)   
...             ...                                     ...   
25281         Zenvo                 Zenvo ST1 (2009 - 2017)   
25282         Zenvo                 Zenvo ST1 (2009 - 2017)   
25283         Zenvo                 Zenvo ST1 (2009 - 2017)   
25284         Zenvo                 Zenvo ST1 (2009 - 2017)   
25285         Zenvo                 Zenvo ST1 (2009 - 2017)   

                                               Image URL  
0      https://s1.cdn.autoevolution.com/images/galler...  
1      https://s1.cdn.autoevolution.com/images/galler...  
2      https://s1.cdn.autoevolution.com/images/galler...  
3      https://s1.cdn.autoevolution.com/images/galler...  
4      https://s1.cdn.autoevolution.com/images/galler...  
...                                                  ...  
25281  https://s1.cdn.autoevolution.com/images/galler...  
25282  https://s1.cdn.autoevolution.com/images/galler...  
25283  https://s1.cdn.autoevolution.com/images/galler...  
25284  https://s1.cdn.autoevolution.com/images/galler...  
25285  https://s1.cdn.autoevolution.com/images/galler...  

[25286 rows x 3 columns]

# Naming excel file with timestamp

In [30]:
now = datetime.datetime.now()
name = "bigImage " + str(now) + ".xlsx"
name = name.replace(":", "-")

# Output in Excel

In [33]:
# Create a Pandas Excel writer using XlsxWriter as the engine.
writer = pd.ExcelWriter(name, engine='xlsxwriter')

## Output Brands - Models - Variants

In [32]:
# Write each dataframe to a different worksheet.

brand_overview.to_excel(writer, sheet_name='Brands')
model_overview.to_excel(writer, sheet_name='Models')
# variant_overview.to_excel(writer, sheet_name='Variants')
# bigImage_overview.to_excel(writer, sheet_name='BigImage')

writer.save()

# Download Thumbnails

In [ ]:
# brandList[1]
# variantImgUrlList[0]
# len(variantImgUrlList)

In [ ]:
def down(url, dest_folder):
    if not os.path.exists(dest_folder):
        os.makedirs(dest_folder)  # create folder if it does not exist

    filename = url.split('/')[-1].replace(" ", "_")  # be careful with file names
    file_path = os.path.join(dest_folder, filename)

    r = requests.get(url, stream=True)
    if r.ok:
        print("saving to", os.path.abspath(file_path))
        with open(file_path, 'wb') as f:
            for chunk in r.iter_content(chunk_size=1024 * 8):
                if chunk:
                    f.write(chunk)
                    f.flush()
                    os.fsync(f.fileno())
    else:  # HTTP status code 4XX/5XX
        print("Download failed: status code {}\n{}".format(r.status_code, r.text))

for i in range(len(variantImgUrlList)):
    url = variantImgUrlList[i]
    dest_folder = 'Autoevolution Thumbnails/' + variantBrandList[i] + '/' + variantModelList[i]
    down(url, dest_folder)

# Download Big Images

In [ ]:
for i in range(len(bigImageUrl)):
    url = bigImageUrl[i]
    dest_folder = 'Autoevolution Big Images/' + bigImageBrand[i] + '/' + bigImageTitle[i]
    down(url, dest_folder)

# IMPORT IMAGES

## define downloader

In [12]:
def down(url, dest_folder):
    if not os.path.exists(dest_folder):
        os.makedirs(dest_folder)  # create folder if it does not exist

    filename = url.split('/')[-1].replace(" ", "_")  # be careful with file names
    file_path = os.path.join(dest_folder, filename)

    r = requests.get(url, stream=True)
    if r.ok:
        print("saving to", os.path.abspath(file_path))
        with open(file_path, 'wb') as f:
            for chunk in r.iter_content(chunk_size=1024 * 8):
                if chunk:
                    f.write(chunk)
                    f.flush()
                    os.fsync(f.fileno())
    else:  # HTTP status code 4XX/5XX
        print("Download failed: status code {}\n{}".format(r.status_code, r.text))

## Import brand informations from excel file

In [13]:
brandL = []
brandLogoUrlL = []

brandL.clear()
brandLogoUrlL.clear()

brandL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Brands')['Brand'].values.tolist()
brandLogoUrlL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Brands')['Brand Logo URL'].values.tolist()

print (brandL, brandLogoUrlL)
print(len(brandL), len(brandLogoUrlL))

['AC ', 'ACURA', 'ALFA ROMEO', 'ALPINE', 'ARIEL', 'ARO', 'ARTEGA', 'ASTON MARTIN', 'AUDI', 'AURUS', 'BENTLEY', 'BMW', 'BRISTOL', 'BUFORI', 'BUGATTI', 'BUICK', 'CADILLAC', 'CATERHAM', 'CHEVROLET', 'CHRYSLER', 'CITROEN', 'CUPRA', 'DACIA', 'DAEWOO', 'DAIHATSU', 'DATSUN', 'DeLorean', 'DODGE', 'DONKERVOORT', 'DR MOTOR', 'DS AUTOMOBILES', 'EAGLE', 'FERRARI', 'FIAT', 'FISKER', 'FORD', 'FSO', 'GEELY', 'GENESIS', 'GMC', 'GTA Motor', 'HINDUSTAN', 'HOLDEN', 'HONDA', 'HUMMER', 'HYUNDAI', 'INFINITI', 'ISUZU', 'JAGUAR', 'JEEP', 'Karma', 'KIA', 'KOENIGSEGG', 'KTM', 'LADA', 'LAMBORGHINI', 'LANCIA', 'LAND ROVER', 'LEXUS', 'LINCOLN', 'LOTUS', 'Lucid Motors', 'Mahindra', 'MARUSSIA', 'MARUTI SUZUKI', 'MASERATI', 'MAYBACH', 'MAZDA', 'MCLAREN', 'MERCEDES BENZ', 'Mercedes-AMG', 'MERCURY', 'MG', 'MINI', 'MITSUBISHI', 'MORGAN', 'NIO', 'NISSAN', 'OLDSMOBILE', 'OPEL', 'PAGANI', 'PANOZ', 'PERODUA', 'PEUGEOT', 'Pininfarina', 'PLYMOUTH', 'Polestar', 'PONTIAC', 'PORSCHE', 'PROTON', 'QOROS', 'RAM Trucks', 'RENAULT', 

In [14]:
for i in range(len(brandL)):
    url = brandLogoUrlL[i]
    dest_folder = 'Autoevolution/Brand Logo/'
    down(url, dest_folder)

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/AC /ac-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ACURA/acura-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ALFA ROMEO/alfa-romeo-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ALPINE/alpine-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ARIEL/ariel-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ARO/aro-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ARTEGA/artega-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/ASTON MARTIN/aston-martin-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/AUDI/audi-sm.jpg
saving to /Users/toprak/Pycha

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/NIO/nio-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/NISSAN/nissan-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/OLDSMOBILE/oldsmobile-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/OPEL/opel-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/PAGANI/pagani-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/PANOZ/panoz-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/PERODUA/perodua-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/PEUGEOT/peugeot-sm.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Brand Logo/Pininfarina/pininfarina-sm.jpg
saving to /Users/t

## Import model informations from excel file

In [15]:
mBrandL = []
modelL = []
mImgUrlL = []

mBrandL.clear()
modelL.clear()
mImgUrlL.clear()

mBrandL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Models')['Brand'].values.tolist()
modelL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Models')['Model'].values.tolist()
mImgUrlL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Models')['Model Image URL'].values.tolist()

print (mBrandL, modelL, mImgUrlL)
print(len(mBrandL), len(modelL), len(mImgUrlL))

['AC ', 'AC ', 'AC ', 'AC ', 'AC ', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALPINE', 'ALPINE', 'ALPINE', 'ALPINE', 'ARIEL', 'ARIEL'

In [16]:
for i in range(len(mBrandL)):
    url = mImgUrlL[i]
    dest_folder = 'Autoevolution/Model Images/' + mBrandL[i]
    down(url, dest_folder)

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AC /AC-_Ace-1993_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AC /AC-_Aceca-1998_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AC /AC-_Cobra-378-MkIV-2020_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AC /AC-_428-Convertible-1966_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AC /AC-_428-Coupe-1966_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ACURA/ACURA_MDX-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ACURA/ACURA_RDX-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ACURA/ACURA

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA_ROMEO_Arna-1-5-TI-1983_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA_ROMEO_Brera-2006_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA_ROMEO_Crosswagon-Q4-2004_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA-ROMEO_Giulietta-Quadrifoglio-Verde-2011_main.png_tmb.png
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA_ROMEO_GT-2004_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA_ROMEO_GTV-2003_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ALFA ROMEO/ALFA-ROMEO_MiTo-2016_main.jpg_tmb.

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ASTON MARTIN/ASTON-MARTIN_Rapide-S-2013_main.png_tmb.png
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ASTON MARTIN/ASTON-MARTIN_V12-Vantage-AMR-2017_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ASTON MARTIN/ASTON-MARTIN_V8-Vantage-N420-Roadster-2010_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ASTON MARTIN/ASTON-MARTIN_Vanquish-2012_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ASTON MARTIN/ASTON-MARTIN_Vanquish-S-2016_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/ASTON MARTIN/ASTON-MARTIN_Vanquish-Volante-2013_main.png_tmb.png
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AS

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_Q3-Sportback-2019_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_SQ8-TDI-2019_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_e-tron-Sportback-2019_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_e-tron-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_SQ5-Sportback-2020_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_e-tron-GT-quattro-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/AUDI/AUDI_100-Coupe-S-1970_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Au

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_X3-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_2-Series-Coupe-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_2-Series-Active-Tourer-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_X4-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_4-Series-Gran-Coupe--G26--2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_i8-2018_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/BMW/BMW_6-Series-Gran-Turismo-2020_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolut

...

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/SUZUKI/SUZUKI_X90-1996_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/SUZUKI/SUZUKI_XL7-2007_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TATA MOTORS/TATA-MOTORS_Safari-Storm-2011_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TATA MOTORS/TATA-MOTORS_Indigo-Manza-2009_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TATA MOTORS/TATA-MOTORS_Harrier-2018_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TATA MOTORS/TATA-MOTORS_Nexon-2017_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TATA MOTORS/TATA-MOTORS_Sumo-2008_main.jpg_tmb.jpg
saving to /Users/topra

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_Aqua-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_Corolla-Touring-Sports-2019_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_Prius-Prime-2016_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_GR-86-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_Verso-S-2010_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_Harrier-2014_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/TOYOTA/TOYOTA_Aygo-X-2021_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/ju

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Agila-2008_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Antara-2010_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Astra-Sport-Hatch-2004_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Astra-Twin-Top-2006_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Astra-VXR-2012_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Corsa-WXR-2011_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VAUXHALL/VAUXHALL_Crossland-X-2017_main.jpg_tmb.jpg
saving to /Users/to

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_e-Golf-2016_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_Touran-2015_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_Gol-2014_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_Scirocco-R-2014_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_Scirocco-2014_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_Sharan-2010_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLKSWAGEN/VOLKSWAGEN_Polo-Sedan-2010_main_tmb.jpg
saving to /Users/

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_S60-Polestar-2017_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_C40-Recharge-2022_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_V60-Polestar-2017_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_142-1967_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_144-1967_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_145-1967_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Images/VOLVO/VOLVO_244-1980_main.jpg_tmb.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Model Im

## Import variant informations from excel file

In [18]:
vBrandL = []
vModelL = []
vImgUrlL = []

vBrandL.clear()
vModelL.clear()
vImgUrlL.clear()

vBrandL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Variants')['Variant Brand'].values.tolist()
vModelL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Variants')['Variant Model'].values.tolist()
vImgUrlL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='Variants')['Variant Image URL'].values.tolist()

print (vBrandL, vModelL, vImgUrlL)
print(len(vBrandL), len(vModelL), len(vImgUrlL))

['AC ', 'AC ', 'AC ', 'AC ', 'AC ', 'AC ', 'AC ', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ACURA', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'ALFA ROMEO', 'AL

In [19]:
for i in range(len(vBrandL)):
    url = vImgUrlL[i]
    dest_folder = 'Autoevolution/Variant Images/' + vBrandL[i]
    down(url, dest_folder)

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_Ace-1993_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_Aceca-1998_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_Cobra-MkIII-1965_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_Cobra-378-MkIV-2020_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_Cobra-MkII-1963_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_428-Convertible-1966_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/AC /AC-_428-Coupe-1966_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ACURA/ACURA_MDX-2021_main.jpg
saving to /Use

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Giulietta-Spider-1955_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Giulietta-Sprint-1954_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA-ROMEO_Giulia-2016_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Giulia-Coupe-1300-GTA-Junior-1968_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Giulia-Berlina-1962_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA-ROMEO_4C-2013_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA-ROMEO_4C-Spider-2015_main.jpg
saving to /Us

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Alfetta-1982_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Alfetta-GTV-1980_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Alfetta-GT-1974_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Alfetta-1975_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Arna-1-5-TI-1983_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Brera-2006_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ALFA ROMEO/ALFA_ROMEO_Crosswagon-Q4-2004_main.jpg
saving to /Users/toprak/PycharmProjects/

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON_MARTIN_V8-Coupe-1996_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON_MARTIN_V8-Vantage-1992_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON_MARTIN_V8-Vantage-1977_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON_MARTIN_V8-1969_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_DBS-Superleggera-Volante-2019_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_DBS-Superleggera-2018_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_DBS-2008_main.jpg
sav

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_Vanquish-2001_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_Vanquish-S-2016_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON_MARTIN_V12-Vanquish-S-2004_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_Vanquish-Volante-2013_main.png
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_Vantage-GT12-2015_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON-MARTIN_Virage-2011_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/ASTON MARTIN/ASTON_MARTIN_Virage-Coupe-1988_main.jp

...

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-GTD-5-Doors-2013_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-GTD-3-Doors-2013_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_GTD-2009_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-GTD-2009_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_GTi-2008_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-GTi-5-Doors-2008_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-V-GTI-2003_main.jpg
saving to /Users/toprak/PycharmP

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-VII-3-Doors-2017_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-VII-3-Doors-2012_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-VI-3-Doors-2008_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-V-3-Doors-2003_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-IV--3-doors--1997_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-III-3-Doors--1991_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-II--3-doors--1983_m

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Taigo-2021_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_ID-3-1st-Edition-2019_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Atlas-Cross-Sport-2019_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Golf-GTD-Variant-2015_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Tiguan-2021_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Vento-2010_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLKSWAGEN/VOLKSWAGEN_Ameo-2016_main.jpg
saving to /Users/toprak/PycharmProj

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_XC40-Recharge-2019_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_XC40-2017_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_XC60-Polestar-2017_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_V90-Cross-Country-2019_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_V90-Cross-Country-2016_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S90-2019_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S90-2016_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_C70-COnvertible-1999_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_C70-Coupe-1998_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_P-1800-1961_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S40-2007_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S40-2004_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S40-2000_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S40-1996_main.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Variant Images/VOLVO/VOLVO_S60-Cross-Country-2015_main.j

## Import big image informations from excel file

In [29]:
bBrandL = []
bTitleL = []
bImgUrlL = []

bBrandL.clear()
bTitleL.clear()
bImgUrlL.clear()

bBrandL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='BigImages')['Brand'].values.tolist()
bTitleL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='BigImages')['Title'].values.tolist()
bImgUrlL = pd.read_excel(r'aEvo_2022.xlsx', sheet_name='BigImages')['ImageURL'].values.tolist()

print(len(bBrandL), len(bTitleL), len(bImgUrlL))
# print (bBrandL, bTitleL, bImgUrlL)

219932 219932 219932


In [ ]:
for i in range(len(bBrandL)):
    url = bImgUrlL[i]
    dest_folder = 'Autoevolution/Big Images/' + bBrandL[i] + '/' + bTitleL[i]
    down(url, dest_folder)

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Ace (1993 - 1996)/ac-ace-1993-7215_1.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Ace (1993 - 1996)/ac-ace-1993-7215_2.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Ace (1993 - 1996)/ac-ace-1993-7215_3.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Ace (1993 - 1996)/ac-ace-1993-7215_4.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Ace (1993 - 1996)/ac-ace-1993-7215_5.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Ace (1993 - 1996)/ac-ace-1993-7215_6.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  Aceca (1998 - 2000)/ac-aceca-1998-7214_1.jpg
saving to /Users/toprak/PycharmProjects/pyth

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 Convertible (1966 - 1971)/ac-428-convertible-1966-7054_24.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 Coupe (1966 - 1973)/ac-428-coupe-1966-7055_4.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 Coupe (1966 - 1973)/ac-428-coupe-1966-7055_5.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 Coupe (1966 - 1973)/ac-428-coupe-1966-7055_6.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 Coupe (1966 - 1973)/ac-428-coupe-1966-7055_7.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 Coupe (1966 - 1973)/ac-428-coupe-1966-7055_8.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/AC /AC  428 

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX A-Spec (2018 - Present)/ACURA-MDX-A-Spec-6304_20.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX A-Spec (2018 - Present)/ACURA-MDX-A-Spec-6304_21.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX A-Spec (2018 - Present)/ACURA-MDX-A-Spec-6304_22.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX A-Spec (2018 - Present)/ACURA-MDX-A-Spec-6304_23.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX A-Spec (2018 - Present)/ACURA-MDX-A-Spec-6304_24.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX A-Spec (2018 - Present)/ACURA-MDX-A-Spec-6304_25.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Au

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2016 - 2021)/ACURA-MDX-5611_18.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2016 - 2021)/ACURA-MDX-5611_1.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2016 - 2021)/ACURA-MDX-5611_2.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2016 - 2021)/ACURA-MDX-5611_7.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2016 - 2021)/ACURA-MDX-5611_8.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2013 - 2016)/ACURA-MDX-4836_1.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2013 - 2016)/ACURA-MDX-4836_2.jpg
saving to /Users/toprak/PycharmPr

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURAMDX-4382_20.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURAMDX-4382_21.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURAMDX-4382_22.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURA-MDX-4382_41.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURAMDX-4382_23.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURAMDX-4382_24.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ACURA/ACURA MDX (2010 - 2013)/ACURAMDX-4382_25.jpg
saving to /Users/toprak/PycharmPr

...

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO Giulietta Quadrifoglio Verde (2011 - 2016)/ALFA-ROMEO-Giulietta-Quadrifoglio-Verde-4591_66.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO Giulietta Quadrifoglio Verde (2011 - 2016)/ALFA-ROMEO-Giulietta-Quadrifoglio-Verde-4591_67.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO Giulietta Quadrifoglio Verde (2011 - 2016)/ALFA-ROMEO-Giulietta-Quadrifoglio-Verde-4591_68.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO Giulietta Quadrifoglio Verde (2011 - 2016)/ALFA-ROMEO-Giulietta-Quadrifoglio-Verde-4591_69.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO Giulietta Quadrifoglio Verde (2011 - 2016)/ALFA-ROMEO-Giulietta-Quadrifogli

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO GT (2003 - 2010)/ALFA-ROMEO-GT-16_28.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO GT (2003 - 2010)/ALFA-ROMEO-GT-16_29.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO GT (2003 - 2010)/ALFA-ROMEO-GT-16_30.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO GT (2003 - 2010)/ALFA-ROMEO-GT-16_31.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO GT (2003 - 2010)/ALFA-ROMEO-GT-16_32.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO GT (2003 - 2010)/ALFA-ROMEO-GT-16_33.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/AL

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2016 - 2018)/ALFA-ROMEO-MiTo-6197_11.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2016 - 2018)/ALFA-ROMEO-MiTo-6197_12.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2016 - 2018)/ALFA-ROMEO-MiTo-6197_13.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2016 - 2018)/ALFA-ROMEO-MiTo-6197_14.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2016 - 2018)/ALFA-ROMEO-MiTo-6197_15.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2016 - 2018)/ALFA-ROMEO-MiTo-6197_16.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Au

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2013 - 2016)/ALFA-ROMEO-MiTo-5593_53.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2013 - 2016)/ALFA-ROMEO-MiTo-5593_54.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2013 - 2016)/ALFA-ROMEO-MiTo-5593_55.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2013 - 2016)/ALFA-ROMEO-MiTo-5593_56.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2013 - 2016)/ALFA-ROMEO-MiTo-5593_57.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2013 - 2016)/ALFA-ROMEO-MiTo-5593_58.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Au

saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2008 - 2013)/ALFA-ROMEO-MiTo-3694_28.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2008 - 2013)/ALFA-ROMEO-MiTo-3694_29.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2008 - 2013)/ALFA-ROMEO-MiTo-3694_30.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2008 - 2013)/ALFA-ROMEO-MiTo-3694_31.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2008 - 2013)/ALFA-ROMEO-MiTo-3694_42.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Autoevolution/Big Images/ALFA ROMEO/ALFA ROMEO MiTo (2008 - 2013)/ALFA-ROMEO-MiTo-3694_43.jpg
saving to /Users/toprak/PycharmProjects/pythonProject/jupyter/Au

In [5]:
print("Kod sonu, teşekkürler...")

Kod sonu, teşekkürler...
